In [1]:
import os
from os import listdir
import pandas as pd
import numpy as np
import glob
import cv2
import json
from os.path import expanduser
import splitfolders
import shutil
from define_path import Def_Path

from tqdm import tqdm

import torch 
import torchvision
from torchvision import models
from torchvision.models.detection.rpn import AnchorGenerator
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn 
import torchvision.transforms as T
from torchvision.transforms import functional as F
from torchsummary import summary
from torch.cuda.amp import GradScaler, autocast
from sklearn.model_selection import train_test_split

import albumentations as A # Library for augmentations

import matplotlib.pyplot as plt 
from PIL import Image

import transforms, utils, engine, train
from utils import collate_fn
from engine import train_one_epoch, evaluate


t = torch.cuda.get_device_properties(0).total_memory
print(t)
torch.cuda.empty_cache()

r = torch.cuda.memory_reserved(0)
print(r)
a = torch.cuda.memory_allocated(0)
print(a)
# f = r-a  # free inside reserved

10504699904
0
0


In [2]:
# to generalize home directory. User can change their parent path without entering their home directory
path = Def_Path()

parent_path =  path.home + "/Pictures/" + "Data/"

root_dir = parent_path + path.year + "-" + path.month + "-" + path.day + "/"

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
# torch.cuda.set_per_process_memory_fraction(0.9, 0)
print(device)

cuda


In [4]:
# this fucntion tranforms an input image for diverseifying data for training
def train_transform():
    return A.Compose([
        A.Sequential([
            A.RandomRotate90(p=1), 
            A.RandomBrightnessContrast(brightness_limit=0.3, contrast_limit=0.2, brightness_by_max=True, always_apply=False, p=1), 
        ], p=1),
        A.Resize(640, 480),  # Resize every image to 640x480 after all other transformations
    ],
    keypoint_params=A.KeypointParams(format='xy'),
    bbox_params=A.BboxParams(format='pascal_voc', label_fields=['bboxes_labels'])
    )

In [5]:
def train_test_split(src_dir):
    dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_img) and os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_img)
        os.mkdir(dst_dir_anno)
        
    for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
        shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = parent_path + "split_folder_output" + "-" + path.year + "-" + path.month + "-" + path.day 
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(.7, .2, .1), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
    shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  
    

In [6]:
class KPDataset(Dataset):
    def __init__(self, root, transform=None, demo=False):                
        self.root = root
        self.transform = transform
        self.demo = demo # Use demo=True if you need transformed and original images (for example, for visualization purposes)
        self.imgs_files = sorted(os.listdir(os.path.join(root, "images")))
        self.annotations_files = sorted(os.listdir(os.path.join(root, "annotations")))
    
    def __getitem__(self, idx):
        img_file = self.imgs_files[idx]
        img_path = os.path.join(self.root, "images", self.imgs_files[idx])
        annotations_path = os.path.join(self.root, "annotations", self.annotations_files[idx])

        img_original = cv2.imread(img_path)
        img_original = cv2.cvtColor(img_original, cv2.COLOR_BGR2RGB)
        
        with open(annotations_path) as f:
            data = json.load(f)
            bboxes_original = data['bboxes']
            keypoints_original = data['keypoints']
            
            # All objects are keypoints on the robot
            bboxes_labels_original = [] 
            bboxes_labels_original.append('base_joint')
            bboxes_labels_original.append('joint2')
            bboxes_labels_original.append('joint3')
            bboxes_labels_original.append('joint4')
            bboxes_labels_original.append('joint5')
            bboxes_labels_original.append('joint6')  

        if self.transform:   
            # Converting keypoints from [x,y,visibility]-format to [x, y]-format + Flattening nested list of keypoints            
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]], where each keypoint is in [x, y]-format            
            # Then we need to convert it to the following list:
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2]
            keypoints_original_flattened = [el[0:2] for kp in keypoints_original for el in kp]
            
            # Apply augmentations
            transformed = self.transform(image=img_original, bboxes=bboxes_original, bboxes_labels=bboxes_labels_original, keypoints=keypoints_original_flattened)
            img = transformed['image']
            bboxes = transformed['bboxes']
            # Unflattening list transformed['keypoints']
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2], where each keypoint is in [x, y]-format
            # Then we need to convert it to the following list:
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]]
            keypoints_transformed_unflattened = np.reshape(np.array(transformed['keypoints']), (-1,1,2)).tolist()

            # Converting transformed keypoints from [x, y]-format to [x,y,visibility]-format by appending original visibilities to transformed coordinates of keypoints
            keypoints = []
            for o_idx, obj in enumerate(keypoints_transformed_unflattened):
#                 print("object", obj)
#                 print(" obj index", o_idx)# Iterating over objects
                obj_keypoints = []
                for k_idx, kp in enumerate(obj): # Iterating over keypoints in each object
                    obj_keypoints.append(kp + [keypoints_original[o_idx][k_idx][2]])
                keypoints.append(obj_keypoints)
        
        else:
            img, bboxes, keypoints = img_original, bboxes_original, keypoints_original        
        
        # Convert everything into a torch tensor        
        bboxes = torch.as_tensor(bboxes, dtype=torch.float32)       
        target = {}
        labels = [1, 2, 3, 4, 5, 6]            
        target["boxes"] = bboxes
        target["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are joint positions
        target["image_id"] = torch.tensor([idx])
        target["area"] = (bboxes[:, 3] - bboxes[:, 1]) * (bboxes[:, 2] - bboxes[:, 0])
        target["iscrowd"] = torch.zeros(len(bboxes), dtype=torch.int64)
        target["keypoints"] = torch.as_tensor(keypoints, dtype=torch.float32)
        img = F.to_tensor(img)        
        bboxes_original = torch.as_tensor(bboxes_original, dtype=torch.float32)
        target_original = {}
        target_original["boxes"] = bboxes_original
        target_original["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are glue tubes
        target_original["image_id"] = torch.tensor([idx])
        target_original["area"] = (bboxes_original[:, 3] - bboxes_original[:, 1]) * (bboxes_original[:, 2] - bboxes_original[:, 0])
        target_original["iscrowd"] = torch.zeros(len(bboxes_original), dtype=torch.int64)
        target_original["keypoints"] = torch.as_tensor(keypoints_original, dtype=torch.float32)        
        img_original = F.to_tensor(img_original)

        if self.demo:
            return img, target, img_original, target_original
        else:
            return img, target
    
    def __len__(self):
        return len(self.imgs_files)

In [7]:
import torch.nn as nn

class VanillaGNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(VanillaGNN, self).__init__()
        self.fc1 = nn.Linear(input_dim, hidden_dim)
        self.fc2 = nn.Linear(hidden_dim, output_dim)

    def forward(self, nodes, edges):
        # Aggregate neighboring node features
        summed_neighbor_nodes = torch.zeros_like(nodes)
        for (src, dest) in edges:
            summed_neighbor_nodes[dest] += nodes[src]

        # Pass through neural network layers
        out = torch.relu(self.fc1(summed_neighbor_nodes))
        out = self.fc2(out)
        return out


In [9]:
class CombinedModel(nn.Module):
    def __init__(self):
        super(CombinedModel, self).__init__()
        self.keypoint_rcnn = torchvision.models.detection.keypointrcnn_resnet50_fpn(pretrained=False, pretrained_backbone=True, num_keypoints=6, num_classes=7)
        self.gnn1 = VanillaGNN(2, 64, 64)
        self.gnn2 = VanillaGNN(64, 64, 64)
        self.gnn3 = VanillaGNN(64, 64, 2)
    
    def complete_missing_keypoints(self, keypoints, labels, num_expected_keypoints=6):

        detected_kps = keypoints.shape[0]
        # Check if all keypoints are detected
        if detected_kps == num_expected_keypoints:
            return keypoints

        # Create a placeholder tensor for keypoints with the correct shape
        ordered_keypoints = torch.zeros((num_expected_keypoints, 3), device=keypoints.device)

        # Fill the keypoints as per their labels
        for i, label in enumerate(labels):
            ordered_keypoints[label - 1] = keypoints[i]

        updated = True  # Flag to keep track if we updated any keypoint in the iteration

        while updated:
            updated = False  # Reset for each iteration
            # Loop through all keypoints and check if any is missing
            for i in range(num_expected_keypoints):
                # Check if keypoint is missing
                if torch.sum(ordered_keypoints[i]) == 0:
                    # Handle the edge case for the first and last keypoints
                    if i == 0:
                        prev_keypoint = ordered_keypoints[-1]
                        next_keypoint = ordered_keypoints[i+1]
                    elif i == num_expected_keypoints - 1:
                        prev_keypoint = ordered_keypoints[i-1]
                        next_keypoint = ordered_keypoints[0]
                    else:
                        prev_keypoint = ordered_keypoints[i-1]
                        next_keypoint = ordered_keypoints[i+1]

                    # If either of the neighbors is present
                    if torch.sum(prev_keypoint) != 0 or torch.sum(next_keypoint) != 0:
                        # Compute the average position of the available neighbors
                        average_kp = (prev_keypoint + next_keypoint) / 2.0
                        ordered_keypoints[i] = average_kp
                        updated = True  # We found a keypoint to fill, so set flag to True

        return ordered_keypoints
    
    
    def get_edge_features(self):
        
        edges = torch.tensor([[0, 1], [1, 2], [2, 3], [3, 4], [4, 5], [5, 0]])
        return edges
    

    def forward(self, images, adj_matrix=None, targets=None, train=False):
        if train:
            output = self.keypoint_rcnn(images, targets)
            return output
    
        else:
            all_keypoints = []
            with torch.no_grad():
                self.keypoint_rcnn.eval()
                output = self.keypoint_rcnn(images)
                self.keypoint_rcnn.train()
                
                keypoints = output[0]['keypoints'].detach().cpu().numpy()
                kp_score = output[0]['keypoints_scores'].detach().cpu().numpy()
                labels = output[0]['labels'].detach().cpu().numpy()
                unique_labels = list(set(labels))
                scores = output[0]['scores'].detach().cpu().numpy()
                print("labels", unique_labels)
                kps = []
                kp_scores = []
                ulabels = []

                for label in unique_labels:
                    indices = [j for j, x in enumerate(labels) if x == label]
                    scores_for_label = [scores[j] for j in indices]
                    max_score_index = indices[scores_for_label.index(max(scores_for_label))]
                    kp_score_label = kp_score[max_score_index].tolist()
                    kps.append(keypoints[max_score_index][kp_score_label.index(max(kp_score_label))])
                    ulabels.append(label)

                kps = [torch.tensor(kp, dtype=torch.float32) for kp in kps]
                if not kps:
                    default_value = torch.tensor([[320, 240, 1]], dtype=torch.float32, device=images[i].device)
                    keypoints = default_value.repeat(6, 1)
                else:
                    keypoints = torch.stack(kps)
                        
                print("kp before placeholder", keypoints)
                keypoints = self.complete_missing_keypoints(keypoints, unique_labels)[:, 0:2].to(device)
                print("kp after placeholder", keypoints)
                edges = self.get_edge_features().to(device)
                keypoints = self.gnn1(keypoints, edges)
                print("kp first layer", keypoints)
                keypoints = self.gnn2(keypoints, edges)
                print("kp second layer iteration", keypoints)
                keypoints = self.gnn3(keypoints, edges)
#                 keypoints = nn.functional.relu(keypoints)
                print("kp after graph", keypoints)
            print("All keypoints", keypoints)

            return keypoints

In [ ]:
# Initialize model and optimizer
model = CombinedModel()
model = model.cuda()
optimizer = optim.Adam(model.parameters(), lr=0.0001, weight_decay=0.0001)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.1)

num_epochs = 1
batch_size = 4

KEYPOINTS_FOLDER_TRAIN = train_test_split(root_dir) +"/train" #train_test_split(root_dir) +"/train"
KEYPOINTS_FOLDER_VAL = train_test_split(root_dir) +"/val"
KEYPOINTS_FOLDER_TEST = train_test_split(root_dir) +"/test"

dataset_train = KPDataset(KEYPOINTS_FOLDER_TRAIN, transform=train_transform(), demo=False)
dataset_val = KPDataset(KEYPOINTS_FOLDER_VAL, transform=None, demo=False)
dataset_test = KPDataset(KEYPOINTS_FOLDER_TEST, transform=None, demo=False)

data_loader_train = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn, pin_memory=True)
data_loader_val = DataLoader(dataset_val, batch_size=1, shuffle=False, collate_fn=collate_fn)
data_loader_test = DataLoader(dataset_test, batch_size=1, shuffle=False, collate_fn=collate_fn)

# Initialize the GradScaler for mixed precision training
scaler = GradScaler()

top_5_models = []

model.train()
mse_loss = nn.MSELoss()

for epoch in range(num_epochs):  # for 50 epochs
    for batch_idx, batch in enumerate(data_loader_train):
        images, targets = batch          
        # Move images to GPU
        images = torch.stack(images).cuda()
        imgs = [img.to(device) for img in images]  # Create list of images
        # Move targets to GPU
        for target in targets:
            for key, val in target.items():
                target[key] = val.cuda()
        
        optimizer.zero_grad()
        individual_losses = []
        
       # Automatic mixed precision for forward pass
        with autocast():
            output_train = model(images, targets=targets, train=True)
    
            for i in range(len(images)):
                img = images[i].unsqueeze(0).to(device)
                ground_truth_keypoints = targets[i]['keypoints'].to(device).squeeze()[:,0:2]
                print("ground truth keypoints shape", ground_truth_keypoints)
                optimizer.zero_grad()
                # automatic precision for forward pass
                predicted_keypoints = model(img, train=False)    
                # Compute the loss for this image
                # Compute loss
                loss = mse_loss(predicted_keypoints, ground_truth_keypoints)
                individual_losses.append(loss.item())
            
            # Aggregate the individual losses to get a scalar loss
            scalar_loss = sum(individual_losses) / len(individual_losses)      
            loss_keypoint = output_train['loss_keypoint']
            
            total_loss = scalar_loss + 0.01*loss_keypoint  
            print("total_loss", total_loss)
        
        # Scale the loss and backpropagate
        scaler.scale(total_loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        scheduler.step()
        scaler.step(optimizer)
        scaler.update()
        
        # Check if the current model should be saved as a top model
        if len(top_5_models) < 5 or loss.item() < max(top_5_models, key=lambda x: x[0])[0]:
            # Save the model state and loss
            model_state = {
                'epoch': epoch,
                'complete_model': model,
#                 'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss.item(),
            }
            top_5_models.append((loss.item(), model_state))

            # Sort the list based on loss (ascending order)
            top_5_models.sort(key=lambda x: x[0])

            # If there are more than 5 models, remove the one with the highest loss
            if len(top_5_models) > 5:
                top_5_models.pop()

        print(f"Epoch {epoch+1}/{num_epochs}, Batch {batch_idx + 1}/{len(data_loader_train)}, Loss: {total_loss.item()}")
        
    print(f"Epoch {epoch+1}/{num_epochs}, Loss: {total_loss.item()}")
    
# After all epochs, save the top 5 models to disk
for idx, (_, model_state) in enumerate(top_5_models):
    torch.save(model_state, f'/home/jc-merlab/Pictures/Data/trained_models/vanilla_gnn_model_b{batch_size}_e{num_epochs}_{idx+1}.pth')

/home/jc-merlab/.local/lib/python3.8/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/jc-merlab/.local/lib/python3.8/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
/home/jc-merlab/.local/lib/python3.8/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained_backbone' is deprecated since 0.13 and may be removed in the future, please use 'weights_backbone' instead.
  warnings.warn(
/home/jc-merlab/.local/lib/python3.8/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights_backbone' are deprecated since 0.13 and may be removed in the fu

ground truth keypoints shape tensor([[112.0801, 257.9522],
        [195.9869, 257.9597],
        [225.2600, 183.7926],
        [244.6073, 191.4178],
        [325.6737, 248.4115],
        [331.7459, 269.6038]], device='cuda:0')
labels [3, 4, 6]
kp before placeholder tensor([[263.5374, 181.0311,   1.0000],
        [209.1561, 198.2713,   1.0000],
        [ 67.3240, 203.6850,   1.0000]])
kp after placeholder tensor([[ 33.6620, 101.8425],
        [148.5997, 141.4368],
        [263.5374, 181.0311],
        [209.1561, 198.2713],
        [138.2400, 200.9781],
        [ 67.3240, 203.6850]], device='cuda:0')
kp first layer tensor([[  55.5000,  -19.0938,  -53.3438,  -32.7500,  -26.7188,    5.7109,
           59.3750,  -38.6562,  -16.9531,  -57.4062,   33.1875,   53.7188,
           48.0625,   39.6562,   -3.4414,    3.8652,   -1.9609,  -33.9688,
           20.6250,   -9.1562,    2.5098,  -34.7500,   24.1094,  -27.7656,
          -57.4688,  -10.6562,  -21.0312,   20.2812,   23.0000,    5.9883,
    

labels [3, 4, 6]
kp before placeholder tensor([[410.7024, 423.2162,   1.0000],
        [348.6103, 411.5298,   1.0000],
        [395.9159, 433.4825,   1.0000]])
kp after placeholder tensor([[197.9580, 216.7413],
        [304.3302, 319.9787],
        [410.7024, 423.2162],
        [348.6103, 411.5298],
        [372.2631, 422.5062],
        [395.9159, 433.4825]], device='cuda:0')
kp first layer tensor([[ 1.3462e+02, -4.9469e+01, -2.2012e+02, -1.3075e+02, -3.6250e+01,
          3.5594e+01,  1.0481e+02, -1.6388e+02, -3.3688e+01, -8.2750e+01,
          1.1988e+02,  1.2794e+02,  1.2962e+02,  1.0256e+02, -7.2000e+01,
          2.6391e+01, -6.3469e+01, -8.8062e+01,  7.8625e+01, -6.2000e+01,
          3.9656e+01, -1.0294e+02,  3.2188e+01,  1.1219e+01, -1.1544e+02,
         -3.2688e+01,  1.4102e+01,  1.3525e+02, -3.2594e+01,  3.7031e+01,
         -4.9500e+01,  2.9703e+01,  5.6781e+01,  1.8344e+01,  2.1281e+01,
          4.3094e+01, -6.8562e+01,  1.1369e+02, -6.4297e+00, -5.5430e+00,
         -6.54

/home/jc-merlab/.local/lib/python3.8/site-packages/torch/optim/lr_scheduler.py:138: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "


Epoch 1/1, Batch 1/233, Loss: 75821.40625
ground truth keypoints shape tensor([[366.9199, 381.0478],
        [283.0131, 381.0403],
        [207.6120, 406.6650],
        [200.9221, 386.9881],
        [103.3005, 369.7316],
        [ 88.1376, 354.4572]], device='cuda:0')
labels [3, 4, 6]
kp before placeholder tensor([[ 88.7772, 360.2568,   1.0000],
        [211.3891, 406.4474,   1.0000],
        [468.4187, 110.9430,   1.0000]])
kp after placeholder tensor([[234.2094,  55.4715],
        [161.4933, 207.8642],
        [ 88.7772, 360.2568],
        [211.3891, 406.4474],
        [339.9039, 258.6952],
        [468.4187, 110.9430]], device='cuda:0')
kp first layer tensor([[  79.3125,   22.6875, -274.0000, -145.7500,   32.3438,   26.8750,
          131.7500, -208.8750,   51.4688,   -4.0312,  145.2500,   46.9375,
           67.6875,   81.6250, -140.7500,   29.7656, -107.1875,  -15.5312,
          -14.9844,  -65.1875,  118.1250,  -25.2344,  -11.9609,    3.6074,
          -42.3438,  -55.1875,  108.6

...

labels [3, 4]
kp before placeholder tensor([[ 64.8495, 176.8184,   1.0000],
        [292.4679, 553.8647,   1.0000]])
kp after placeholder tensor([[ 52.7708, 113.4377],
        [ 32.4247,  88.4092],
        [ 64.8495, 176.8184],
        [292.4679, 553.8647],
        [146.2339, 276.9323],
        [ 73.1170, 138.4662]], device='cuda:0')
kp first layer tensor([[  40.3125,  -16.2031,  -44.9062,  -23.6719,  -19.0000,    6.9492,
           34.7500,  -32.9062,  -13.7969,  -35.7188,   26.3594,   40.0000,
           33.6250,   26.7188,   -9.2812,    3.9102,   -6.6367,  -26.0625,
           21.2812,  -10.6484,    4.4219,  -27.6094,   16.2031,  -11.2969,
          -36.5625,   -8.0234,  -10.4453,   22.4844,    5.8906,    7.3281,
          -24.8594,    8.1797,   12.0938,   -1.5898,   11.5234,    7.5820,
          -34.2500,   39.7188,   18.1719,    2.5098,  -18.5000,   28.0312,
            1.6885,  -18.1250,   13.1016,  -71.9375,   10.7578,  -37.8438,
          -29.4375,    4.4062,  -17.3125,  -12.64

ground truth keypoints shape tensor([[193.4642, 489.2265],
        [193.4698, 377.3508],
        [158.7948, 290.8215],
        [171.4949, 274.7382],
        [182.3124, 143.8211],
        [172.4914, 118.0853]], device='cuda:0')
labels [3, 4, 6]
kp before placeholder tensor([[179.6228, 271.1947,   1.0000],
        [190.6136, 108.9632,   1.0000],
        [424.6216, 536.4300,   1.0000]])
kp after placeholder tensor([[212.3108, 268.2150],
        [195.9668, 269.7048],
        [179.6228, 271.1947],
        [190.6136, 108.9632],
        [307.6176, 322.6966],
        [424.6216, 536.4300]], device='cuda:0')
kp first layer tensor([[ 1.6088e+02, -6.1750e+01, -2.4012e+02, -1.3650e+02, -5.4250e+01,
          4.2344e+01,  1.2381e+02, -1.7538e+02, -4.8281e+01, -1.1200e+02,
          1.3375e+02,  1.5975e+02,  1.5412e+02,  1.1738e+02, -7.5125e+01,
          2.8094e+01, -6.3750e+01, -1.0894e+02,  9.7312e+01, -6.6750e+01,
          3.7656e+01, -1.2438e+02,  5.0250e+01,  2.9434e+00, -1.4112e+02,
         

labels [3, 4, 6]
kp before placeholder tensor([[175.8872, 241.7422,   1.0000],
        [161.2743, 225.7263,   1.0000],
        [425.1885, 538.2260,   1.0000]])
kp after placeholder tensor([[212.5943, 269.1130],
        [194.2407, 255.4276],
        [175.8872, 241.7422],
        [161.2743, 225.7263],
        [293.2314, 381.9761],
        [425.1885, 538.2260]], device='cuda:0')
kp first layer tensor([[ 1.6125e+02, -6.1938e+01, -2.4050e+02, -1.3675e+02, -5.4438e+01,
          4.2406e+01,  1.2419e+02, -1.7562e+02, -4.8438e+01, -1.1231e+02,
          1.3412e+02,  1.6025e+02,  1.5450e+02,  1.1762e+02, -7.5188e+01,
          2.8109e+01, -6.3844e+01, -1.0919e+02,  9.7625e+01, -6.6875e+01,
          3.7719e+01, -1.2475e+02,  5.0406e+01,  2.8457e+00, -1.4150e+02,
         -3.5844e+01, -1.5344e-01,  1.4650e+02, -2.3172e+01,  4.1469e+01,
         -7.3688e+01,  3.1641e+01,  5.7125e+01,  1.6781e+01,  2.7891e+01,
          5.2000e+01, -1.0094e+02,  1.4900e+02,  1.6375e+01,  1.3066e+00,
         -7.71

ground truth keypoints shape tensor([[112.0801, 257.9522],
        [195.9869, 257.9597],
        [271.7372, 282.4057],
        [265.3756, 302.1683],
        [287.5673, 398.6889],
        [308.4815, 394.2321]], device='cuda:0')
labels [1, 3, 4, 6]
kp before placeholder tensor([[308.6868, 434.6958,   1.0000],
        [293.8592, 393.8278,   1.0000],
        [260.2125, 297.6062,   1.0000],
        [ 67.6905, 205.4991,   1.0000]])
kp after placeholder tensor([[308.6868, 434.6958],
        [301.2730, 414.2618],
        [293.8592, 393.8278],
        [260.2125, 297.6062],
        [163.9515, 251.5526],
        [ 67.6905, 205.4991]], device='cuda:0')
kp first layer tensor([[ 5.6000e+01, -1.9234e+01, -5.3781e+01, -3.3031e+01, -2.6953e+01,
          5.7344e+00,  6.0000e+01, -3.8938e+01, -1.7078e+01, -5.7938e+01,
          3.3469e+01,  5.4188e+01,  4.8469e+01,  4.0031e+01, -3.4004e+00,
          3.8867e+00, -1.9512e+00, -3.4281e+01,  2.0750e+01, -9.2031e+00,
          2.5254e+00, -3.5062e+01,  2.43

labels [3, 4, 6]
kp before placeholder tensor([[409.2271, 423.4917,   1.0000],
        [356.9930, 397.1204,   1.0000],
        [456.3112,  28.9133,   1.0000]])
kp after placeholder tensor([[228.1556,  14.4567],
        [318.6913, 218.9742],
        [409.2271, 423.4917],
        [356.9930, 397.1204],
        [406.6521, 213.0169],
        [456.3112,  28.9133]], device='cuda:0')
kp first layer tensor([[ 6.8312e+01,  3.6812e+01, -2.6975e+02, -1.3575e+02,  4.4125e+01,
          2.2000e+01,  1.4150e+02, -2.1725e+02,  7.3438e+01,  4.0664e+00,
          1.2838e+02,  3.1219e+01,  4.8531e+01,  7.1500e+01, -1.4062e+02,
          2.5844e+01, -1.0369e+02, -2.8438e+00, -4.4156e+01, -5.3281e+01,
          1.2850e+02, -5.2148e+00, -1.7891e+01,  5.2031e+00, -2.9297e+01,
         -4.8219e+01,  1.3212e+02,  1.3600e+02, -8.7375e+01, -2.3953e+01,
          9.4688e+01,  3.2188e+01,  8.8312e+01, -2.0266e+01,  1.0578e+01,
         -3.4590e+00,  4.6219e+01,  7.1000e+01, -7.6875e+01,  2.2656e+00,
          2.51

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as func
import networkx as nx


class GNNEncoder(nn.Module):
    def __init__(self, vertices_dim=3, hidden_dim=128, num_vertices=6, num_edge_features=2):
        super(GNNEncoder, self).__init__()
        self.f_enc = nn.Linear(vertices_dim, hidden_dim)
        self.f_e1 = nn.Linear((hidden_dim * 2), hidden_dim)
        self.f_v = nn.Linear(hidden_dim, hidden_dim)
        self.f_e2 = nn.Linear((hidden_dim * 2), num_edge_features)
        self.num_vertices = num_vertices        
    
#     def get_node_features(self, vertices):
# #         print("Vertices in node features", vertices)
#         node_features = []
#         for keypoint in vertices:
#             x, y, confidence, visibility, label = keypoint
#             node_features.append([x, y, confidence, visibility, label])        
#         nodes = torch.tensor(node_features, dtype=torch.float).to(device)
# #         print(nodes)
#         return nodes

    def get_edge_features(self, vertices):
        edges = [(0,1), (1, 2), (2, 3), (3, 4), (4, 5), (5, 0)]
#         print(edges)
#         edge_features = []
#         for edge in edges:
#             print(edge)
#             print(edge[0])
#             print(edge[1])
#             k1, k2 = vertices[edge[0]][:2], vertices[edge[1]][:2]
#             distance = torch.norm(k1 - k2)
#             angle = torch.atan2(k2[1] - k1[1], k2[0] - k1[0])
#             edge_features.append([distance.item(), angle.item()])
            
        edges = torch.tensor(edges, dtype=torch.long).to(device)
#         edge_features = torch.tensor(edge_features, dtype=torch.float).to(device)
#         return edges, edge_features
        return edges

    def forward(self, vertices):
        vertices = vertices.to(device)
        edges = self.get_edge_features(vertices)
        h1 = self.f_enc(vertices)
        h1_source = h1[edges[:, 0]]
        h1_target = h1[edges[:, 1]]
        h_e1 = self.f_e1(torch.cat((h1_source, h1_target), dim=-1))
        h_j_2 = self.f_v(h_e1)
        h2_source = h_j_2[edges[:, 0]]
        h2_target = h_j_2[edges[:, 1]]
        h_e2 = self.f_e2(torch.cat((h2_source, h2_target), dim=-1))
        h_e2_prob = torch.sigmoid(h_e2)
        return vertices, h_e2_prob, edges

class GNNDecoder(nn.Module):
    def __init__(self, vertices_dim=3, hidden_dim=128, num_vertices=6, num_edge_features=2):
        super(GNNDecoder, self).__init__()
        self.f_e = nn.Linear((vertices_dim * 2), num_edge_features)  # Concatenate two vertices features
        self.f_h = nn.Linear(num_edge_features, vertices_dim)  # Transform h_ij to the same dimension as vertices
        self.f_v = nn.Linear(vertices_dim, vertices_dim)  # Update vertex feature
    
    def forward(self, vertices, h_e2_prob, edges):
        h_source = vertices[edges[:, 0]]
        h_target = vertices[edges[:, 1]]
        h = torch.zeros_like(vertices)

        for idx, (i, j) in enumerate(edges):  # Iterate over edges 
            h_ij = h_e2_prob[idx] * self.f_e(torch.cat((h_source[idx].unsqueeze(0), h_target[idx].unsqueeze(0)), dim=1))  # Include edge weights in the input
            h_ij_transformed = self.f_h(h_ij.squeeze())  # Transform h_ij to the same dimension as vertices
            h[j] += h_ij_transformed  # Accumulate edge features to the target vertex

        h_transformed = self.f_v(h.view(-1, vertices.shape[1]))  # Transform h
        h_transformed = h_transformed.view(vertices.shape)  # Reshape back to original shape
        vertices_g = vertices + h_transformed  # Update vertex features

        return vertices_g  # Return vertices_g as the prediction and vertices_g itself as the mean for Gaussian distribution



In [ ]:
def occ_keypoints_loss(vertices_pred, vertices_gt, edges_prob, edges_gt):
#     huber_loss = nn.SmoothL1Loss()
    mse_loss = nn.MSELoss()
    # Compute the loss
    kp_loss = mse_loss(vertices_pred[:,:2], vertices_gt[:,:2])
    print("kp_loss", kp_loss)
    vis_loss = nn.functional.cross_entropy(vertices_pred[:,2:], vertices_gt[:,2:])
    print("vis_loss", vis_loss)
    edge_loss = loss = -torch.sum(edges_gt.to(device) * torch.log(torch.clamp(edges_prob, min=1e-7)))   
    print("edge_loss", edge_loss)
    
    return kp_loss+vis_loss+edge_loss
    
# def visibility_loss (vertices_pred, vertices_gt):    
#     return nn.functional.cross_entropy(vertices_pred[:,:,:2], vertices_gt[:,:,:2])  # Loss based on visibility of keypoints

# def edge_loss(edges_prob, edges_gt):
#     # Compute the cross-entropy loss
#     loss = -torch.sum(edges_gt.to(device) * torch.log(torch.clamp(edges_prob, min=1e-7)))                      
#     return loss

In [ ]:
class CombinedModel(nn.Module):
    def __init__(self):
        super().__init__()

        self.keypoint_rcnn = torchvision.models.detection.keypointrcnn_resnet50_fpn(pretrained=False, pretrained_backbone=True, num_keypoints=6, num_classes=7)
        self.gnn_encoder = GNNEncoder()
        self.gnn_decoder = GNNDecoder()
        
    def complete_missing_keypoints(self, keypoints, labels, num_expected_keypoints=6):

        detected_kps = keypoints.shape[0]
        # Check if all keypoints are detected
        if detected_kps == num_expected_keypoints:
            return keypoints

        # Create a placeholder tensor for keypoints with the correct shape
        ordered_keypoints = torch.zeros((num_expected_keypoints, 3), device=keypoints.device)

        # If some keypoints are detected, compute their average position
        average_kp = torch.mean(keypoints, dim=0, keepdim=True)

        for i, label in enumerate(labels):
            ordered_keypoints[label - 1] = keypoints[i]
            
        # Fill in the missing keypoints with the average position
        missing_indices = (torch.sum(ordered_keypoints, dim=1) == 0).nonzero(as_tuple=True)[0]
        ordered_keypoints[missing_indices] = average_kp
        
        return ordered_keypoints

    def forward(self, images, targets=None, train=False):
        if train:
            output = self.keypoint_rcnn(images, targets)
            return output
    
        else:
            all_keypoints = []
            all_edges = []
            with torch.no_grad():
                self.keypoint_rcnn.eval()
                output = self.keypoint_rcnn(images)
                self.keypoint_rcnn.train()
                
                keypoints = output[0]['keypoints'].detach().cpu().numpy()
                kp_score = output[0]['keypoints_scores'].detach().cpu().numpy()
                labels = output[0]['labels'].detach().cpu().numpy()
                unique_labels = list(set(labels))
                scores = output[0]['scores'].detach().cpu().numpy()
                print("labels", unique_labels)

                kps = []
                kp_scores = []
                ulabels = []
                
                for label in unique_labels:
                    indices = [j for j, x in enumerate(labels) if x == label]
                    scores_for_label = [scores[j] for j in indices]
                    max_score_index = indices[scores_for_label.index(max(scores_for_label))]
                    kp_score_label = kp_score[max_score_index].tolist()
                    kps.append(keypoints[max_score_index][kp_score_label.index(max(kp_score_label))])
                    ulabels.append(label)

                kps = [torch.tensor(kp, dtype=torch.float32) for kp in kps]
                if not kps:
                    default_value = torch.tensor([[320, 240, 1]], dtype=torch.float32, device=images[i].device)
                    keypoints = default_value.repeat(6, 1)
                else:
                    keypoints = torch.stack(kps)
                        
                print("kp before placeholder", keypoints)
                keypoints = self.complete_missing_keypoints(keypoints, unique_labels)
                print("kp after placeholder", keypoints)
                vertices, self.enc_e, self.edges = self.gnn_encoder(keypoints)
                vertices_pred = self.gnn_decoder(vertices, self.enc_e, self.edges)
                edges_pred = self.enc_e
                edges = self.edges


            print("All keypoints", vertices_pred)

            return vertices_pred, edges_pred, edges
    

In [ ]:
# Initialize model and optimizer
model = CombinedModel()
model = model.cuda()
optimizer = optim.Adam(model.parameters(), lr=0.0001, weight_decay=0.0001)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.1)

num_epochs = 50
batch_size = 4

KEYPOINTS_FOLDER_TRAIN = train_test_split(root_dir) +"/train" #train_test_split(root_dir) +"/train"
KEYPOINTS_FOLDER_VAL = train_test_split(root_dir) +"/val"
KEYPOINTS_FOLDER_TEST = train_test_split(root_dir) +"/test"

dataset_train = KPDataset(KEYPOINTS_FOLDER_TRAIN, transform=train_transform(), demo=False)
dataset_val = KPDataset(KEYPOINTS_FOLDER_VAL, transform=None, demo=False)
dataset_test = KPDataset(KEYPOINTS_FOLDER_TEST, transform=None, demo=False)

data_loader_train = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn, pin_memory=True)
data_loader_val = DataLoader(dataset_val, batch_size=1, shuffle=False, collate_fn=collate_fn)
data_loader_test = DataLoader(dataset_test, batch_size=1, shuffle=False, collate_fn=collate_fn)

# Initialize the GradScaler for mixed precision training
scaler = GradScaler()

top_5_models = []

model.train()

for epoch in range(num_epochs):  # for 50 epochs
    for batch_idx, batch in enumerate(data_loader_train):
        images, targets = batch          
        # Move images to GPU
        images = torch.stack(images).cuda()
        imgs = [img.to(device) for img in images]  # Create list of images
        # Move targets to GPU
        for target in targets:
            for key, val in target.items():
                target[key] = val.cuda()
        
        optimizer.zero_grad()
        individual_losses = []
        
       # Automatic mixed precision for forward pass
        with autocast():
            output_train = model(images, targets=targets, train=True)
    
            for i in range(len(images)):
                img = images[i].unsqueeze(0) 
                ground_truth_keypoints = targets[i]['keypoints'].to(device).squeeze()
                print("ground truth keypoints shape", ground_truth_keypoints)
                optimizer.zero_grad()
                # automatic precision for forward pass
                predicted_keypoints, predicted_edges, ground_truth_edges = model(img, train=False)    
                # Compute the loss for this image
                # Compute loss
                loss = occ_keypoints_loss(predicted_keypoints, ground_truth_keypoints, predicted_edges, ground_truth_edges)
                individual_losses.append(loss.item())
            
            # Aggregate the individual losses to get a scalar loss
            scalar_loss = sum(individual_losses) / len(individual_losses)      
            loss_keypoint = output_train['loss_keypoint']
            print("loss keypoint", loss)
            total_loss = scalar_loss + 0.01*loss_keypoint           
        
        # Scale the loss and backpropagate
        scaler.scale(total_loss).backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        scheduler.step()
        scaler.step(optimizer)
        scaler.update()
        
        # Check if the current model should be saved as a top model
        if len(top_5_models) < 5 or loss.item() < max(top_5_models, key=lambda x: x[0])[0]:
            # Save the model state and loss
            model_state = {
                'epoch': epoch,
                'complete_model': model,
#                 'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss.item(),
            }
            top_5_models.append((loss.item(), model_state))

            # Sort the list based on loss (ascending order)
            top_5_models.sort(key=lambda x: x[0])

            # If there are more than 5 models, remove the one with the highest loss
            if len(top_5_models) > 5:
                top_5_models.pop()

        print(f"Epoch {epoch+1}/{num_epochs}, Batch {batch_idx + 1}/{len(data_loader_train)}, Loss: {loss.item()}")
        
    print(f"Epoch {epoch+1}/{num_epochs}, Loss: {loss.item()}")
    
# After all epochs, save the top 5 models to disk
for idx, (_, model_state) in enumerate(top_5_models):
    torch.save(model_state, f'/home/jc-merlab/Pictures/Data/trained_models/vanilla_gnn_model_b{batch_size}_e{num_epochs}_{idx+1}.pth')